In [29]:
import matplotlib.pyplot as plt
from math import sin, cos
import numpy as np
from matplotlib.animation import FFMpegWriter
metadata = dict(title='Oumuamua Simulation', artist='Matplotlib',comment='Oh my')
writer = FFMpegWriter(fps=15, metadata=metadata)
import warnings

In [30]:
# Conversion functions between actual space distances and pixels in matplotlib
def pix2au(pix):
    conversion_factor = 1.496e+11 / 20
    return pix * conversion_factor

def au2pix(au):
    conversion_factor = 20 / 1.496e+11
    return au * conversion_factor

### Initialize coordinate positions of the sun, planet, and asteroids

In [31]:
ms=1e7
mp=1e4
ms=1.9891e30
mp=5.972e+24

ma=2.589e20
G=6.67e-11
# G=1
R=pix2au(20)

xp = R - (((ms+mp)/mp)**-1 * R)
yp = 0
theta_p = np.radians(0)

xs = -(R - (((ms+mp)/mp)**-1 * R)) * (mp/ms)
ys = 0
theta_s = np.radians(180)

theta_a = np.radians(45)
xa = R*cos(theta_a)
ya = R*sin(theta_a) 

### Calculate mu and omega

In [32]:
mu = (mp*ms)/(mp+ms)
omega = np.sqrt((G*mp*ms)/(mu*R**3))
rp = np.sqrt(xp**2 + yp**2)
rs = np.sqrt(xs**2 + ys**2)
ra = np.sqrt(xa**2 + ya**2)

### Initialize the velocities of all celestial bodies

In [33]:
vp = omega*rp
vpx = vp*sin(theta_p)
vpy = vp*cos(theta_p)

vs = omega*rs
vsx = vs*sin(theta_s)
vsy = vs*cos(theta_s)

va = omega*ra
vax = -va*sin(theta_a)
vay = va*cos(theta_a)

### The Kepler ODE Function

In [34]:
def KeplerODE(t,y,ma=1):
    global mp,ms,G
    global go
    global count
    rs, rp, ra = y[0:2], y[4:6], y[8]
    vs, vp, va = y[2:4], y[6:8], y[9]
    
    def force(m1, m2, r1, r2):
        global G
        global count
        try:
            norms = (np.linalg.norm((r1-r2).astype('float'), axis=1))**3
            top = (- m1 * m2 * G * (r1-r2).T).T
            F = (top.T / norms).T
            return F
        except np.AxisError:
            norm = (np.linalg.norm(r1-r2))**3
            top = - m1 * m2 * G * (r1-r2)
            return - m1 * m2 * G / norm * (r1-r2)
    
    # Movement of the sun
    # Get the current velocity of the sun
    drdt_s = vs 
    # Calculate the force between the sun and the planet
    Fsp = force(ms, mp, rs, rp)
    # Calculate the force between the sun and the asteroid
    Fsa = force(ms, ma, rs, ra)
    # Sum up all of the forces
    try:
        Fsa = np.sum(Fsa, axis=0)
    except np.AxisError:
        pass
    Fs = Fsp+Fsa
    # Calculate the acceleration from the force
    as_ = Fs/ms
    # Apply this acceleration
    dvdt_s = as_
    
    # Movement of the planet
    drdt_p = vp
    Fps = force(mp, ms, rp, rs)
    Fpa = force(mp, ma, rp, ra)
    try:
        Fpa = np.sum(Fpa, axis=0)
    except np.AxisError:
        pass
    Fp = Fps+Fpa
    ap = Fp/mp 
    dvdt_p = ap
    
    # Movement of the asteroid
    drdt_a = va
    Fas = force(ma, ms, ra, rs)
    Fap = force(ma, mp, ra, rp)
    Fa = Fas+Fap
    aa = (Fa.T/ma).T
    dvdt_a = aa

    diff = np.concatenate((drdt_s,dvdt_s,drdt_p,dvdt_p)) 
    diff = list(diff)
    diff.append(drdt_a)
    diff.append(dvdt_a)
    return np.array(diff)

### Rescaling Notes
* 1 AU = 1.496e+11 m ~ 20 coordinates 

In [35]:
# Conversion functions between actual space distances and pixels in matplotlib
def downscale(Y):
    newY = np.copy(Y)
    return au2pix(newY)

def upscale(Y):
    newY = np.copy(Y)
    return pix2au(newY)

In [36]:
# Choose the random seed
seed = 101
np.random.seed(seed)

# number of asteroids
N = int(1e6)

# Create an adjustable quantity of asteroids
ou_coords = np.random.uniform(-1.6*rp, 1.6*rp, (N,2))
ou_vels = np.random.uniform(-9000, 9000, (N,2))
MA = np.random.uniform(8e5, 8e7, (N))

# Create an asteroid in the Lagrange point for sanity check
ou_coords = np.concatenate((ou_coords, np.array([[xa, ya], [-xa, ya]])))
ou_vels = np.concatenate((ou_vels, np.array([[vax, vay], [-vax, vay]])))
MA = np.concatenate((MA, [8e7, 8e5]))

In [37]:
# Renaming numpy funcs
both = np.logical_and
or_ = np.logical_or

In [ ]:
warnings.filterwarnings("ignore") 
sr = 6.95700e8 # solar radius

# Initialize matrix for KeplerODE
Y = np.array([xs, ys, vsx, vsy, xp, yp, vpx, vpy, ou_coords, ou_vels])

# Initialize time variables
P = np.sqrt(((4*np.pi**2)/(G*(mp+ms)))*R**3)
dt = P/1000
t = 0

# Initialize figure
fig = plt.figure(figsize=(12.,6.), dpi=200)


with writer.saving(fig, "kepler.mp4", dpi=200):
    while t < (P/2):
        plt.clf()
        F_1 = KeplerODE(t,Y,MA)
        F_2 = KeplerODE(t+(dt/2), Y+((dt/2)*F_1), MA)
        F_3 = KeplerODE(t+(dt/2), Y+((dt/2)*F_2), MA)
        F_4 = KeplerODE(t+dt, Y+(dt*F_3), MA)
        Y += (dt/6)*(F_1 + 2*F_2 + 2*F_3 + F_4)
        t += dt
        
        # Remove objects that crash into the Sun
        tempY = np.copy(Y[9])
        try:
            idxs = np.where(or_(np.absolute(tempY[:,0]) > 300000, np.absolute(tempY[:,1]) > 300000))[0][0]
            tempY = np.delete(tempY, idxs, axis=0)
            Y[9] = tempY

            tempY = np.copy(Y[8])
            tempY = np.delete(tempY, idxs, axis=0)
            Y[8] = tempY

            tempM = np.copy(MA)
            tempM = np.delete(tempM, idxs)
            MA = tempM
        except IndexError:
            pass
        
        scaleY = downscale(Y)
        
        plt.axvline(x=au2pix(-1.496e11), color='red', alpha=0.3)
        plt.axvline(x=au2pix(1.496e11), color='red', alpha=0.3)
        plt.axhline(y=au2pix(-1.496e11), color='red', alpha=0.3)
        plt.axhline(y=au2pix(1.496e11), color='red', alpha=0.3)

        plt.plot(scaleY[4], scaleY[5], '.', color='blue', markersize=40)
        plt.plot(scaleY[0], scaleY[1], '.', color='gold', markersize=70)
        plt.plot(scaleY[8][:,0], scaleY[8][:,1], '.', color='red', markersize=10)
        plt.xlim(-30, 30)
        plt.ylim(-30, 30)
        
        writer.grab_frame()